# D) DJI ML - Feature engineering 

In [1]:
#imports
import yfinance as yf
import numpy as np
import pandas as pd
import os
import exchange_calendars as xcals
import matplotlib.pyplot as plt
import seaborn as sns
from statsmodels.tsa.seasonal import seasonal_decompose
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split, TimeSeriesSplit
from sklearn.linear_model import LinearRegression, Ridge
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from scipy.stats import zscore
from scipy.stats.mstats import winsorize
from statsmodels.stats.outliers_influence import variance_inflation_factor
from sklearn.ensemble import RandomForestRegressor
from sklearn.feature_selection import RFE
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from itertools import product
from bayes_opt import BayesianOptimization

In [2]:
#Load data
base_path="C:\\Users\\tgsog\\OneDrive\\Desktop\\DowJones_ML_project\\DataFiles\\"
df =pd.read_csv(base_path+"B) cleaned stock data\\stock_clean_data_fin.csv")

# 3. Feature engineering

### Feature #1: Moving average features (ma(2) to ma(5))

In [3]:
def ma_feat(df,firstMA,lastMA):
    df_MA = pd.DataFrame()
    for x in df.columns:
    ## Moving averages:
        for i in range(firstMA,lastMA):
            df_MA[f"{x}_MA({i})"] =df[x].rolling(window=i).mean()
    ### MA does not need column specific values
    df_MA
    return df_MA

In [4]:
df_ma = ma_feat(df,2,5)

C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\730861365.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_MA[f"{x}_MA({i})"] =df[x].rolling(window=i).mean()
C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\730861365.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_MA[f"{x}_MA({i})"] =df[x].rolling(window=i).mean()
C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\730861365.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor per

### Feature #2: Moving average convergance divergance against signal

In [5]:
def macd(df, long_window, short_window, signal_window):
    df_macd =pd.DataFrame()
    for col in df.columns:
        df_macd[f"{col}_MACD"] = df[col].ewm(span=short_window, adjust=False).mean() - df[col].ewm(span=long_window, adjust=False).mean()
        df_macd[f"{col}_Signal"] = df_macd[f"{col}_MACD"].ewm(span=signal_window, adjust=False).mean()
        df_macd[f"{col}_Histogram"] = df_macd[f"{col}_MACD"] - df_macd[f"{col}_Signal"]
    return df_macd


In [6]:
df_macd =macd(df,20,12,9)

C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\2701960479.py:5: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_macd[f"{col}_Signal"] = df_macd[f"{col}_MACD"].ewm(span=signal_window, adjust=False).mean()
C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\2701960479.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_macd[f"{col}_Histogram"] = df_macd[f"{col}_MACD"] - df_macd[f"{col}_Signal"]
C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\2701960479.py:4: PerformanceWarning: DataFrame is highly fragmented.  This is usual

### Feature #3 Relative strength index

In [7]:
def calc_rsi(df, period=14):
    def rsi_calc(values, period):
        diff = values.diff()
        profit = diff.where(diff > 0, 0)
        loss = diff.where(diff < 0, 0)
        mean_profit = profit.ewm(com=period - 1, adjust=False).mean()
        mean_loss = loss.ewm(com=period - 1, adjust=False).mean()
        rs = mean_profit / mean_loss
        rsi = 100 - (100 / (1 + rs))
        return rsi

    df_rsi = pd.DataFrame(index=df.index)

    for col in df.columns:
        df_rsi[f"{col}_RSI"] = rsi_calc(df[col], period)

    return df_rsi

df_RSI =calc_rsi(df,14)


C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\4290881609.py:15: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_rsi[f"{col}_RSI"] = rsi_calc(df[col], period)
C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\4290881609.py:15: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_rsi[f"{col}_RSI"] = rsi_calc(df[col], period)
C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\4290881609.py:15: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor perform

### Feature #4 :Bollinger bands

In [8]:
def calc_bollinger(df, window=20, multiplier=2):
    bb_df = pd.DataFrame(index=df.index)

    for column in df.columns:
        rolling_mean = df[column].rolling(window=window, min_periods=1).mean()
        rolling_std = df[column].rolling(window=window, min_periods=1).std()

        bb_df[f"{column}_BB_Mid"] = rolling_mean
        bb_df[f"{column}_BB_Upper"] = rolling_mean + (rolling_std * multiplier)
        bb_df[f"{column}_BB_Lower"] = rolling_mean - (rolling_std * multiplier)

    return bb_df

df_bb = calc_bollinger(df,20,2)


C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\1037984222.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  bb_df[f"{column}_BB_Upper"] = rolling_mean + (rolling_std * multiplier)
C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\1037984222.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  bb_df[f"{column}_BB_Lower"] = rolling_mean - (rolling_std * multiplier)
C:\Users\tgsog\AppData\Local\Temp\ipykernel_34612\1037984222.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `fram

### Feature #5: Delta

In [9]:
def delta(df):
    df_delt = df.diff().rename(columns=lambda x: f"delta_{x}")
    return df_delt
df_delta = delta(df)

### Feature #6: Shifting

In [10]:
def shifting(df, shift):
    df_s = df.shift(shift)
    df_s.columns = [f"shift_{shift}_" + col for col in df_s.columns]  # Rename columns
    return df_s
df_shift_1 =shifting(df,1)
df_shift_2 = shifting(df,2)

### Feature #7: Log transformation
To log transform we need to determine
1. If columns have a right skew
2. Apply log() to those variables

In [11]:
def skew_n_log(df, skew_threshold=0.5):
    from scipy.stats import skew
    skew_labels = []
    log_transform_cols = []

    for col in df.columns:
        col_data = df[col].dropna()
        col_skew = skew(col_data)

        # Classify skewness
        if col_skew > skew_threshold:
            skew_type = "Right-Skewed"
        elif col_skew < -skew_threshold:
            skew_type = "Left-Skewed"
        else:
            skew_type = "Symmetric"

        skew_labels.append((col, skew_type))

        # Add to transform list if right-skewed and non-negative
        if skew_type == "Right-Skewed" and (col_data >= 0).all():
            log_transform_cols.append(col)

    # Create skew classification DataFrame
    sk_df = pd.DataFrame(skew_labels, columns=["Column", "Skew"])

    # Create log-transformed DataFrame
    df_log = pd.DataFrame()
    for col in log_transform_cols:
        df_log[f"log_{col}"] = np.log1p(df[col])

    return df_log


In [12]:
df_log =skew_n_log(df,0.5)

### Merging all features with df

In [13]:
def left_merge_on_index(df_list):
    merged_df = df_list[0].copy()
    for df in df_list[1:]:
        merged_df = merged_df.merge(df, how='left', left_index=True, right_index=True)
    return merged_df

df_lis = [df,df_ma, df_macd,df_RSI,df_bb,df_delta,df_shift_1,df_shift_2,df_log]

df_aux = left_merge_on_index(df_lis)
df= df_aux

In [14]:
#Finding the lowest NA value in the df
def get_na_row_indices(df):
    """
    Returns a list of row indices where at least one NaN value is present in the row.
    """
    na_rows = df[df.isnull().any(axis=1)].index.tolist()
    return na_rows


In [15]:
print(f"There are NA values in the rows {get_na_row_indices(df)}")
df = df.dropna()


There are NA values in the rows [0, 1, 2]


In [16]:
df

High_AAPL  High_AMGN  High_AMZN  High_AXP   High_BA  High_CAT  High_CRM  \
3     0.006515   0.007503   0.002178  0.018519  0.010215  0.023618  0.043287   
4    -0.007883   0.003082  -0.012903  0.005564 -0.001869 -0.007419 -0.031545   
5     0.022889  -0.005230   0.022153 -0.014831 -0.000851  0.006536 -0.013523   
6     0.001852  -0.000147  -0.004846 -0.001911  0.019128  0.014813  0.009179   
7     0.001232   0.005332   0.000473 -0.018332 -0.003887 -0.006245 -0.012796   
..         ...        ...        ...       ...       ...       ...       ...   
314   0.008014   0.012507   0.006537  0.007938  0.011911  0.009423  0.003609   
315  -0.016227   0.023489  -0.033690 -0.038522 -0.056166 -0.046618 -0.037681   
316  -0.014662  -0.002752   0.015377 -0.019365 -0.024053  0.022867  0.003532   
317   0.005538  -0.000815  -0.020049 -0.013840 -0.009980  0.007069  0.018450   
318   0.014757   0.029842  -0.017009 -0.028317 -0.026615  0.029862 -0.032776   

     High_CSCO  High_CVX  High_DIS  ...  log_Volume_NKE  log_Volume_NVDA  \
3     0.005773  0.003425 -0.010867  ...       15.901170        19.727166   
4    -0.012300 -0.005529 -0.004632  ...       16.126718        19.896686   
5    -0.004566 -0.004324 -0.006818  ...       15.755690        19.733646   
6     0.005213 -0.007169  0.008390  ...       15.658755        19.757233   
7     0.003112 -0.000139  0.009076  ...       15.802631        19.675792   
..         ...       ...       ...  ...             ...              ...   
314   0.011222  0.008949  0.013685  ...       15.970616        19.835031   
315  -0.014951 -0.037104 -0.028559  ...       16.121500        19.802373   
316   0.004225 -0.018034 -0.011670  ...       16.103348        19.465674   
317  -0.002493  0.012948 -0.019019  ...       16.079739        19.587518   
318   0.002343  0.026870 -0.028117  ...       16.044912        19.649606   

     log_Volume_PG  log_Volume_SHW  log_Volume_TRV  log_Volume_UNH  \
3        15.553271       14.245409       14.189486       15.057271   
4        15.699287       14.291000       14.643233       14.812164   
5        16.291696       14.395937       14.204779       14.788409   
6        15.844974       14.975438       13.981280       14.621853   
7        15.627007       14.469813       13.914633       14.736471   
..             ...             ...             ...             ...   
314      15.845670       14.773826       14.375869       15.556012   
315      16.310170       14.757235       13.956751       15.584360   
316      15.759862       14.508758       13.906540       15.106697   
317      15.717991       14.554587       13.745304       15.417723   
318      16.073799       14.520834       13.781851       15.508205   

     log_Volume_V  log_Volume_VZ  log_Volume_WMT  log_Volume_^DJI  
3       15.186539      16.848462       17.486063        19.589565  
4       15.473263      16.911504       17.029703        19.612935  
5       15.250381      16.951148       16.901257        19.549661  
6       15.169798      16.822109       17.090668        19.461805  
7       15.093468      16.538331       17.048786        19.475968  
..            ...            ...             ...              ...  
314     16.023741      16.921621       16.726349        20.410690  
315     16.007812      17.300666       17.043453        20.519655  
316     15.925021      16.708013       16.685623        20.182582  
317     15.968563      16.944282       16.809131        20.283023  
318     15.665335      17.621997       17.396616        20.453345  

[316 rows x 2999 columns]

## Outlier analysis

### Outlier threshold and detection threshold functions

In [17]:
#Function for detecting which columns have enough outliers to be winsordized
def thresh_percent(df,decimal_percent):
    training_size =len(df)*0.8
    threshold = round(training_size*decimal_percent)
    return threshold

def outlier_detection_and_windsor_w_drop(X_df,outlier_max):
    
    from scipy.stats import zscore
    from scipy.stats.mstats import winsorize

    df_ols_zscores = X_df.apply(zscore)
    X= (df_ols_zscores.abs() > 3)
    outlier_cols=[]
    for col in X.columns:
        if X[col].sum()>=outlier_max:
            outlier_cols.append(col)
    colnames= []
    for col in outlier_cols:
        X_df[col] = winsorize(X_df[col], limits=[0.01, 0.01]) 
        colnames.append(col)
    X_df=X_df.drop(columns=colnames)
    return X_df

# 4. Data scaling / normalization

#Scalers instanciated
scaler_zscore = StandardScaler()
scaler_minmax = MinMaxScaler(feature_range=(0, 1))
def categorize_returns(df, column, threshold=0.00):
    return (df[column] > threshold).astype(int)

In [18]:
#Splitting function
def split_func(df,y_name,bin_o_num, pct_outliers_needed=0.05):
    if bin_o_num == "num":
        y =df[y_name]
    else:
        y =df[y_name].apply(lambda x: 1 if x>0 else 0)
    X=df.drop(columns=[y_name])
    X= outlier_detection_and_windsor_w_drop(X,thresh_percent(X,pct_outliers_needed))
    return X, y

In [19]:
#X Y split  and outlier analysis
X_ols,y_ols = split_func(df,"Close_^DJI", bin_o_num="num", pct_outliers_needed =0.01)
X_lstm,y_lstm = split_func(df,"Close_^DJI",bin_o_num="num", pct_outliers_needed=0.03)

X_nb,y_nb = split_func(df,"Close_^DJI",bin_o_num="bin", pct_outliers_needed = 0.05)
X_gru,y_gru = split_func(df,"Close_^DJI",bin_o_num="bin", pct_outliers_needed=0.03)
X_xg,y_xg = split_func(df,"Close_^DJI",bin_o_num="bin", pct_outliers_needed=0.05)
X_cat,y_cat = split_func(df,"Close_^DJI",bin_o_num="bin", pct_outliers_needed=0.05)

In [20]:
#Timeseries split function:
def ts_train_test_func(X,y,train_pct):
    n_splits = int(1 / (1 - train_pct))  # 1 / 0.2 = 5 splits (for 80% train, 20% test)
    tscv = TimeSeriesSplit(n_splits=n_splits)
    for train_index, test_index in tscv.split(X):
        X_train, X_test = X.iloc[train_index], X.iloc[test_index]
        y_train, y_test = y.iloc[train_index], y.iloc[test_index]
    return X_train, X_test, y_train, y_test

In [21]:
#timeseries splitting into model datasets
X_train_ols,X_test_ols,y_train_ols, y_test_ols =  ts_train_test_func(X_ols,y_ols,0.8)
X_train_lstm,X_test_lstm,y_train_lstm, y_test_lstm =  ts_train_test_func(X_lstm,y_lstm,0.8)
X_train_nb,X_test_nb,y_train_nb, y_test_nb =  ts_train_test_func(X_nb,y_nb,0.8)
X_train_gru,X_test_gru,y_train_gru, y_test_gru =  ts_train_test_func(X_gru,y_gru,0.8)
X_train_xg,X_test_xg,y_train_xg, y_test_xg =  ts_train_test_func(X_xg,y_xg,0.8)
X_train_cat,X_test_cat,y_train_cat, y_test_cat =  ts_train_test_func(X_cat,y_cat,0.8)


### 1/3 Df: OLS model data

In [22]:
#scaling x - either standard scaling or minmax scaling
def x_scaler(X_train, X_test, stand_min):
    from sklearn.preprocessing import MinMaxScaler
    from sklearn.preprocessing import StandardScaler

    if stand_min == "stand":
        scaler_X = StandardScaler().fit(X_train)
        X_train_scaled = scaler_X.transform(X_train)
        X_test_scaled = scaler_X.transform(X_test)
    elif stand_min == "min":
        scaler_X = MinMaxScaler().fit(X_train)
        X_train_scaled = scaler_X.transform(X_train)
        X_test_scaled = scaler_X.transform(X_test)
    return X_train_scaled, X_test_scaled, scaler_X

#Scaling y either, standard scaling or minmax scale
def y_scaler(y_train, y_test, stand_min):
    from sklearn.preprocessing import StandardScaler
    from sklearn.preprocessing import MinMaxScaler

    y_train = y_train.reshape(-1, 1) if isinstance(y_train, np.ndarray) else y_train.values.reshape(-1, 1)
    y_test = y_test.reshape(-1, 1) if isinstance(y_test, np.ndarray) else y_test.values.reshape(-1, 1)

    if stand_min == "stand":
        #Standard scaler y
        scaler_y = StandardScaler().fit(y_train.reshape(-1, 1))
        y_train_scaled = scaler_y.transform(y_train.reshape(-1, 1))
        y_test_scaled = scaler_y.transform(y_test.reshape(-1, 1))
    elif stand_min == "min":
        #Minmax scale y
        scaler_y = MinMaxScaler(feature_range=(0, 1))  # or (-1, 1) if needed
        y_train_scaled = scaler_y.fit_transform(y_train)
        y_test_scaled = scaler_y.transform(y_test)
    return y_train_scaled, y_test_scaled, scaler_y


In [23]:
#Scaling OLS data
X_train_sc_ols, X_test_sc_ols, scaler_X_ols=x_scaler(X_train_ols,X_test_ols, stand_min="stand")
y_train_sc_ols, y_test_sc_ols, scaler_y_ols = y_scaler(y_train_ols, y_test_ols, stand_min="stand")

#Scaling LSTM data
X_train_sc_lstm, X_test_sc_lstm, scaler_X_lstm=x_scaler(X_train_lstm,X_test_lstm, stand_min="min")
y_train_sc_lstm, y_test_sc_lstm, scaler_y_lstm = y_scaler(y_train_lstm, y_test_lstm, stand_min="min")
 
#Scaling Gru data (only X needed)
X_train_sc_gru, X_test_sc_gru, scaler_X_gru=x_scaler(X_train_gru,X_test_gru, stand_min="min")

THe following is completed:
1. splitting into datasets
2. standardizing
What needs to be done:
- Downloading as csv files
- Feature selection is done in the next file

In [24]:
import joblib

## Uploading scalers

In [25]:
scaler_path =base_path+"X1. scalers (from feature engineering)\\"
joblib.dump(scaler_X_ols, scaler_path+'scaler_X_ols.pkl')
joblib.dump(scaler_y_ols, scaler_path+'scaler_y_ols.pkl')
joblib.dump(scaler_X_lstm, scaler_path+'scaler_X_lstm.pkl')
joblib.dump(scaler_y_lstm, scaler_path+'scaler_y_lstm.pkl')
joblib.dump(scaler_X_gru, scaler_path+'scaler_X_gru.pkl')

['C:\\Users\\tgsog\\OneDrive\\Desktop\\DowJones_ML_project\\DataFiles\\X1. scalers (from feature engineering)\\scaler_X_gru.pkl']

# Uploading the datasets

In [26]:
base_path = base_path+"D) feature engineered data\\"

In [27]:
ols_path = base_path+"1. OLS data\\"
# === OLS ===
pd.DataFrame(X_train_sc_ols).to_csv(ols_path+"X_train_ols.csv", index=False)
pd.DataFrame(X_test_sc_ols).to_csv(ols_path+"X_test_ols.csv", index=False)
pd.DataFrame(y_train_sc_ols).to_csv(ols_path+"y_train_ols.csv", index=False)
pd.DataFrame(y_test_sc_ols).to_csv(ols_path+"y_test_ols.csv", index=False)

lstm_path = base_path+"2. LSTM\\"
# === LSTM ===
pd.DataFrame(X_train_sc_lstm).to_csv(lstm_path+"X_train_lstm.csv", index=False)
pd.DataFrame(X_test_sc_lstm).to_csv(lstm_path+"X_test_lstm.csv", index=False)
pd.DataFrame(y_train_sc_lstm).to_csv(lstm_path+"y_train_lstm.csv", index=False)
pd.DataFrame(y_test_sc_lstm).to_csv(lstm_path+"y_test_lstm.csv", index=False)

gru_path= base_path + "3. Gradiant data\\"
# === GRU ===
pd.DataFrame(X_train_sc_gru).to_csv(gru_path+"X_train_gru.csv", index=False)
pd.DataFrame(X_test_sc_gru).to_csv(gru_path+"X_test_gru.csv", index=False)
pd.DataFrame(y_train_gru).to_csv(gru_path+"y_train_gru.csv", index=False)
pd.DataFrame(y_test_gru).to_csv(gru_path+"y_test_gru.csv", index=False)

nb_path = base_path+"3. Naive bayes data\\"
# === Naive Bayes ===
pd.DataFrame(X_train_nb).to_csv(nb_path+"X_train_nb.csv", index=False)
pd.DataFrame(X_test_nb).to_csv(nb_path+"X_test_nb.csv", index=False)
pd.DataFrame(y_train_nb).to_csv(nb_path+"y_train_nb.csv", index=False)
pd.DataFrame(y_test_nb).to_csv(nb_path+"y_test_nb.csv", index=False)

xg_path = base_path+"3. xgboost data\\"
# === XGBoost ===
pd.DataFrame(X_train_xg).to_csv(xg_path+"X_train_xg.csv", index=False)
pd.DataFrame(X_test_xg).to_csv(xg_path+"X_test_xg.csv", index=False)
pd.DataFrame(y_train_xg).to_csv(xg_path+"y_train_xg.csv", index=False)
pd.DataFrame(y_test_xg).to_csv(xg_path+"y_test_xg.csv", index=False)

cat_path = base_path+"3. catboost data\\"
# === CatBoost ===
pd.DataFrame(X_train_cat).to_csv(cat_path+"X_train_cat.csv", index=False)
pd.DataFrame(X_test_cat).to_csv(cat_path+"X_test_cat.csv", index=False)
pd.DataFrame(y_train_cat).to_csv(cat_path+"y_train_cat.csv", index=False)
pd.DataFrame(y_test_cat).to_csv(cat_path+"y_test_cat.csv", index=False)


###### OLS MODEL DATA ######
    #Needs scaled X values, and real Y values for OLS
    #Needs no scaling for GRU/Naive bayes/ random forest




#1.OLS data 
y_ols =df["Close_^DJI"] 
X_ols =df.drop(columns=["Close_^DJI"])

#3. Winsorize outliers 
#we windsorise variables that have 1% or more outliers
outlier_benchmark =round(len(X_ols)*0.01,0)
X_ols = outlier_detection_and_windsor_w_drop(X_ols,outlier_benchmark)

#4. Divide into train and test
# Define Time Series Split
n_splits = int(1 / (1 - 0.8))  # 1 / 0.2 = 5 splits (for 80% train, 20% test)
tscv = TimeSeriesSplit(n_splits=n_splits)
for train_index, test_index in tscv.split(X_ols):
    X_train_ols, X_test_ols = X_ols.iloc[train_index], X_ols.iloc[test_index]
    y_train_ols, y_test_ols = y_ols.iloc[train_index], y_ols.iloc[test_index]

#############################################






#scale
scaler_x_ = StandardScaler()
X_train_ols_s = scaler_x_.fit_transform(X_train_ols)
X_test_ols_s = scaler_x_.transform(X_test_ols)

#Final pearson dataset
X_train_ols  = pd.DataFrame(X_train_ols_s, columns=X_train_ols.columns)
X_test_ols  = pd.DataFrame(X_test_ols_s, columns=X_test_ols.columns)

base_path_o="C:\\Users\\tgsog\\OneDrive\\Desktop\\DowJones_ML_project\\DataFiles\\OLS data\\"

# Add to folder
y_test_ols.to_csv(base_path_o+"y_values\\y_test_ols.csv")
y_train_ols.to_csv(base_path_o+"y_values\\y_train_ols.csv")
X_test_ols.to_csv(base_path_o+"x_values\\X_test_ols.csv")
X_train_ols.to_csv(base_path_o+"x_values\\X_train_ols.csv")



### 2/3 Df: LSTM model data

###### LSTM MODEL DATA ######
    #Needs scaled X values, and  Y values for OLS
y_lstm = df_lstm["Close_^DJI"]
X_lstm =df_lstm.drop(columns=["Close_^DJI"])


#2.LSTM data scaled
y_lstm = pd.DataFrame(scaler_minmax.fit_transform(y_lstm.values.reshape(-1, 1)), columns=["Close_^DJI"], index=y_lstm.index)
X_lstm = pd.DataFrame(scaler_minmax.fit_transform(X_lstm), columns=X_lstm.columns, index=X_lstm.index) 

#6. Divide into train and test:
n_splits = int(1 / (1 - 0.8))  # 1 / 0.2 = 5 splits (for 80% train, 20% test)
tscv = TimeSeriesSplit(n_splits=n_splits)
for train_index, test_index in tscv.split(X_lstm):
    X_train_lstm, X_test_lstm = X_lstm.iloc[train_index], X_lstm.iloc[test_index]
    y_train_lstm, y_test_lstm = y_lstm.iloc[train_index], y_lstm.iloc[test_index]


base_path_lstm="C:\\Users\\tgsog\\OneDrive\\Desktop\\DowJones_ML_project\\DataFiles\\LSTM data\\"

# Add to folder
y_test_lstm.to_csv(base_path_lstm+"y_values\\y_test_lstm.csv")
y_train_lstm.to_csv(base_path_lstm+"y_values\\y_train_lstm.csv")
X_test_lstm.to_csv(base_path_lstm+"x_values\\X_test_lstm.csv")
X_train_lstm.to_csv(base_path_lstm+"x_values\\X_train_lstm.csv")


### 3/3 Df: Direct final data (GRU/Naive/Forests/Catboost/XGboost) 

#### GRU direct data

# Fix categorical
df_gru["y_binary"] = categorize_returns(df_gru,"Close_^DJI",0)
df_gru = df_gru.ffill()

#Fix label
X_gru =df_gru.drop(columns =["y_binary","Close_^DJI"]) 
y_gru =df_gru["y_binary"]

y_gru = pd.DataFrame(scaler_minmax.fit_transform(y_gru.values.reshape(-1, 1)), columns=["y_binary"], index=y_gru.index)
X_gru = pd.DataFrame(scaler_minmax.fit_transform(X_gru), columns=X_gru.columns, index=X_gru.index) 

#Split - time series
n_splits = int(1 / (1 - 0.8))  # 1 / 0.2 = 5 splits (for 80% train, 20% test)
tscv = TimeSeriesSplit(n_splits=n_splits)
for train_index, test_index in tscv.split(X_gru):
    X_train_gru, X_test_gru = X_gru.iloc[train_index], X_gru.iloc[test_index]
    y_train_gru, y_test_gru = y_gru.iloc[train_index], y_gru.iloc[test_index]


base_path_class="C:\\Users\\tgsog\\OneDrive\\Desktop\\DowJones_ML_project\\DataFiles\\Classification model data\\"

# Add to folder
y_test_gru.to_csv(base_path_class+"y_values\\y_test_gru.csv")
y_train_gru.to_csv(base_path_class+"y_values\\y_train_gru.csv")
X_test_gru.to_csv(base_path_class+"x_values\\X_test_gru.csv")
X_train_gru.to_csv(base_path_class+"x_values\\X_train_gru.csv")

print(len(df_gru), len(X_train_gru), len(X_test_gru))

#### Naive bayes direct data

# Fix categorical
df_nb["y_binary"] = categorize_returns(df_nb,"Close_^DJI",0)

# Fix label
X_nb = df_nb.drop(columns=["y_binary","Close_^DJI"]) 
y_nb = df_nb["y_binary"]

# Set train_size to 1036 (same as GRU)
train_size = len(X_train_gru)
X_train_nb, X_test_nb, y_train_nb, y_test_nb = train_test_split(
    X_nb, y_nb, train_size=train_size, test_size=len(X_nb) - train_size, random_state=42, shuffle=False
)

print(len(df_nb), len(X_train_nb), len(X_test_nb))  

y_test_nb.to_csv(base_path_class+"y_values\\y_test_nb.csv")
y_train_nb.to_csv(base_path_class+"y_values\\y_train_nb.csv")
X_test_nb.to_csv(base_path_class+"x_values\\X_test_nb.csv")
X_train_nb.to_csv(base_path_class+"x_values\\X_train_nb.csv")

print(len(df_nb), len(X_train_nb), len(X_test_nb))

#### Cat boost direct data

# Fix categorical
df_cat["y_binary"] = categorize_returns(df_cat,"Close_^DJI",0)

def xg_process(df_cat):
    # Fix label
    X_cat = df_cat.drop(columns=["y_binary","Close_^DJI"]) 
    y_cat = df_cat["y_binary"]

    # Ensure the same split as GRU and NB (1037 train, 208 test)
    train_size = len(X_train_gru)
    X_train_cat, X_test_cat, y_train_cat, y_test_cat = train_test_split(
        X_cat, y_cat, train_size=train_size, test_size=len(X_cat) - train_size, random_state=42, shuffle=False
    )
    
    return X_train_cat, X_test_cat, y_train_cat, y_test_cat

# Apply function
X_train_cat, X_test_cat, y_train_cat, y_test_cat = xg_process(df_cat)

print(len(df_cat), len(X_train_cat), len(X_test_cat))

y_test_cat.to_csv(base_path_class+"y_values\\y_test_cat.csv")
y_train_cat.to_csv(base_path_class+"y_values\\y_train_cat.csv")
X_test_cat.to_csv(base_path_class+"x_values\\X_test_cat.csv")
X_train_cat.to_csv(base_path_class+"x_values\\X_train_cat.csv")

#### XGBoost direct data

# Fix categorical
df_xg["y_binary"] = categorize_returns(df_xg,"Close_^DJI",0)
df_xg = df_xg.ffill()

def xg_process(df_xg):
    #Fix label
    X_xg =df_xg.drop(columns =["y_binary","Close_^DJI"]) 
    y_xg =df_xg["y_binary"]


    #Ts split:
    tscv = TimeSeriesSplit(n_splits=5)
    for train_index, test_index in tscv.split(X_xg):
        X_train_xg, X_test_xg = X_xg.iloc[train_index], X_xg.iloc[test_index]
        y_train_xg, y_test_xg = y_xg.iloc[train_index], y_xg.iloc[test_index]

    return X_train_xg, X_test_xg, y_train_xg, y_test_xg
X_train_xg, X_test_xg, y_train_xg, y_test_xg = xg_process(df_xg)

y_test_xg.to_csv(base_path_class+"y_values\\y_test_xg.csv")
y_train_xg.to_csv(base_path_class+"y_values\\y_train_xg.csv")
X_test_xg.to_csv(base_path_class+"x_values\\X_test_xg.csv")
X_train_xg.to_csv(base_path_class+"x_values\\X_train_xg.csv")

print(len(df_xg), len(X_train_xg), len(X_test_xg))
print(len(df_cat), len(X_train_cat), len(X_test_cat))
print(len(df_nb), len(X_train_nb), len(X_test_nb))
print(len(df_gru), len(X_train_gru), len(X_test_gru))
print(len(df_ols), len(X_train_ols), len(X_test_ols))
print(len(df_lstm), len(X_train_lstm), len(X_test_lstm))